# LOCKED POSITION RANDOMIZED DATA

FILENAME: budget_randomized.ipynb
    
PROJECT: Randomized Data Model

DATE CREATED: 27-MAY-20

DATE UPDATED: 27-MAY-20

## PHASE 1: PROJECT SETUP

In [48]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

Import the necessary libraries needed for ETL, engineering, and export efforts

In [49]:
import pandas as pd
import csv
import random
import sqlite3
import itertools
import numpy as np
import datetime
from itertools import repeat
import time as t
import getpass as gp

# plotting modules
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.offline as po

In [50]:
def init_array(df_length):
    '''
    DESCRIPTION: A function to create and return a two_dimensional array with randomized float values
    '''
    
    length = df_length
    
    num_of_projects = 20 # can change the amount of projects
    num_of_subprojects = 40 # can change the amount of subprojects
    num_of_programs = 80
    num_of_rca = 120 # can change the amount of RCAs
    
    # create a sequential list of column values for projects, subprojects, and RCAs
    proj_list = ['project-' + str(i+1) for i in range(num_of_projects)] # create a list of project names
    subproject_list = ['subproject-' + str(i+1) for i in range(num_of_subprojects)]
    program_list = ['program-' + str(i+1) for i in range(num_of_programs)]
    rca_list = ['rca-' + str(i+1) for i in range(num_of_rca)]
    
    project_values = []
    subproject_values = []
    program_values = []
    rca_values = []

    for index in range(length):
        
        # select a random value from each list
        proj_val = random.choice(proj_list)
        sb_val = (random.choice(subproject_list))
        program_val = random.choice(program_list)
        rca_val = random.choice(rca_list)
        
        # append the randomized value to the default list
        project_values.append(proj_val)
        subproject_values.append(sb_val)
        program_values.append(program_val)
        rca_values.append(rca_val)
    
    # create randomized budget data
    yr3_forecast= np.random.randint(low = 100000, high = 30000000, size = df_length) 
    yr2_random = np.random.uniform(low=0.5, high=1.3, size=df_length)
    yr2_forecast = np.round(yr3_forecast * yr2_random,2)
    
    yr1_random = np.random.uniform(low=0.8, high=1.2, size=df_length)
    yr1_forecast = np.round(yr2_forecast * yr1_random,2)
    
    plan_random = np.random.uniform(low=0.6, high=1.3, size=df_length)
    plan_val = np.round(yr1_forecast * plan_random,2)
    
    approp_random = np.random.uniform(low=0.6, high=1.2, size=df_length)
    approp_val = np.round(plan_val * approp_random,2)
    
    oblig_random = np.random.uniform(low=0.8, high=1.0, size=df_length)
    oblig_val = np.round(approp_val * oblig_random,2)
    
    raw_df = pd.DataFrame(columns=['project', 'subproject', 'program_title', 'rca','yr+3_forecast','yr+2_forecast','yr+1_forecast','yr0_plan','yr-1_approp','yr-2_oblig'])

    raw_df['project'] = project_values
    raw_df['subproject'] = subproject_values
    raw_df['program_title'] = program_values
    raw_df['rca'] = rca_values
    raw_df['yr+3_forecast'] = yr3_forecast
    raw_df['yr+2_forecast'] = yr2_forecast
    raw_df['yr+1_forecast'] = yr1_forecast
    raw_df['yr0_plan'] = plan_val
    raw_df['yr-1_approp'] = approp_val
    raw_df['yr-2_oblig'] = oblig_val
    
    return raw_df

# PHASE 2: FUNCTION TEST

In [51]:
train_df = init_array(10000)
train_df.tail(10)

project     subproject program_title      rca  yr+3_forecast  \
9990  project-20   subproject-5    program-32   rca-53       12256949   
9991  project-19  subproject-31    program-74   rca-19        7915017   
9992  project-19  subproject-21    program-20   rca-57        1162783   
9993  project-12   subproject-4    program-31   rca-48       18193640   
9994   project-3  subproject-13    program-49   rca-22       20651161   
9995  project-20  subproject-14    program-62   rca-58        8619770   
9996   project-1  subproject-22    program-63  rca-103        7538358   
9997   project-4  subproject-14    program-69   rca-99       28258150   
9998   project-9   subproject-4    program-11   rca-58        6182360   
9999  project-17  subproject-34    program-45   rca-80       19379027   

      yr+2_forecast  yr+1_forecast     yr0_plan  yr-1_approp   yr-2_oblig  
9990    13819543.89    15119654.75  18171999.34  19118277.18  17431216.07  
9991     8522616.31     7965513.20   9254161.61   9148834.06   7538662.30  
9992     1219812.83     1430987.42   1488018.17   1098993.71    892388.26  
9993    23468749.94    23849224.63  23141187.85  25809421.31  22864304.91  
9994    25362013.85    29614077.41  38489829.50  41383556.16  40192320.35  
9995     9777582.96    10530202.36  12753294.47  12109364.35  11998330.90  
9996     6159271.36     5561597.87   4568742.58   4994170.18   4482591.34  
9997    32822900.65    37285954.32  32876792.06  37679315.03  35504816.13  
9998     4938432.26     4402621.97   2827732.44   2692945.76   2374555.21  
9999    17355471.88    16736256.45  21611141.00  14990945.22  13832187.69

In [52]:
train_df['key'] = train_df['project'] + '-' + train_df['subproject'] + '-' + train_df['program_title'] + '-' + train_df['rca']
train_df['key']


0       project-13-subproject-9-program-39-rca-120
1         project-9-subproject-27-program-25-rca-7
2       project-15-subproject-24-program-23-rca-92
3       project-1-subproject-21-program-48-rca-119
4       project-9-subproject-36-program-37-rca-116
                           ...                    
9995    project-20-subproject-14-program-62-rca-58
9996    project-1-subproject-22-program-63-rca-103
9997     project-4-subproject-14-program-69-rca-99
9998      project-9-subproject-4-program-11-rca-58
9999    project-17-subproject-34-program-45-rca-80
Name: key, Length: 10000, dtype: object

In [53]:
key_df = train_df[['key']]
duplicateRowsDF = key_df[key_df.duplicated()]
 
print("Duplicate Rows except first occurrence based on all columns are :")
print(duplicateRowsDF)

print("Total count of duplicated rows :")
print(len(duplicateRowsDF))

Duplicate Rows except first occurrence based on all columns are :
                                             key
3031   project-7-subproject-24-program-41-rca-86
7500   project-1-subproject-26-program-34-rca-17
8122   project-2-subproject-19-program-18-rca-87
8675   project-13-subproject-31-program-80-rca-4
9239    project-7-subproject-5-program-41-rca-21
9804  project-2-subproject-39-program-34-rca-104
Total count of duplicated rows :
6


In [54]:
# dropping ALL duplicte values 
train_df.drop_duplicates(subset ="key", 
                     keep = False, inplace = True) 


In [55]:
key_df = train_df[['key']]
duplicateRowsDF = key_df[key_df.duplicated()]
 
print("Duplicate Rows except first occurrence based on all columns are :")
print(duplicateRowsDF)

print("\nTotal count of duplicated rows :",len(duplicateRowsDF))


Duplicate Rows except first occurrence based on all columns are :
Empty DataFrame
Columns: [key]
Index: []

Total count of duplicated rows : 0


### Store unique values in data structures

In [56]:
budget_col_names = list(train_df.columns)
budget_col_names

['project',
 'subproject',
 'program_title',
 'rca',
 'yr+3_forecast',
 'yr+2_forecast',
 'yr+1_forecast',
 'yr0_plan',
 'yr-1_approp',
 'yr-2_oblig',
 'key']

In [57]:
budget_ordinal_names = budget_col_names[:4]
budget_ordinal_names

['project', 'subproject', 'program_title', 'rca']

In [58]:
proj_uniq_values = train_df['project'].unique()
print(set(proj_uniq_values))

{'project-15', 'project-16', 'project-3', 'project-13', 'project-8', 'project-10', 'project-9', 'project-4', 'project-6', 'project-5', 'project-7', 'project-17', 'project-19', 'project-14', 'project-20', 'project-18', 'project-2', 'project-1', 'project-12', 'project-11'}


In [59]:
subproj_uniq_values = train_df['subproject'].unique()
print(set(subproj_uniq_values))

{'subproject-24', 'subproject-40', 'subproject-17', 'subproject-20', 'subproject-23', 'subproject-38', 'subproject-28', 'subproject-14', 'subproject-37', 'subproject-15', 'subproject-12', 'subproject-39', 'subproject-25', 'subproject-36', 'subproject-8', 'subproject-34', 'subproject-19', 'subproject-3', 'subproject-11', 'subproject-18', 'subproject-31', 'subproject-29', 'subproject-30', 'subproject-16', 'subproject-6', 'subproject-9', 'subproject-32', 'subproject-2', 'subproject-33', 'subproject-21', 'subproject-22', 'subproject-27', 'subproject-10', 'subproject-13', 'subproject-26', 'subproject-4', 'subproject-7', 'subproject-35', 'subproject-1', 'subproject-5'}


In [60]:
program_uniq_values = train_df['program_title'].unique()
print(set(program_uniq_values))

{'program-67', 'program-36', 'program-33', 'program-24', 'program-79', 'program-38', 'program-42', 'program-66', 'program-65', 'program-50', 'program-57', 'program-41', 'program-10', 'program-43', 'program-52', 'program-71', 'program-74', 'program-37', 'program-31', 'program-2', 'program-77', 'program-11', 'program-54', 'program-44', 'program-30', 'program-22', 'program-61', 'program-13', 'program-80', 'program-68', 'program-39', 'program-21', 'program-8', 'program-40', 'program-49', 'program-32', 'program-48', 'program-14', 'program-5', 'program-58', 'program-17', 'program-12', 'program-63', 'program-28', 'program-69', 'program-3', 'program-27', 'program-20', 'program-9', 'program-1', 'program-59', 'program-23', 'program-62', 'program-25', 'program-16', 'program-55', 'program-4', 'program-46', 'program-15', 'program-76', 'program-26', 'program-75', 'program-60', 'program-6', 'program-35', 'program-34', 'program-7', 'program-64', 'program-18', 'program-73', 'program-53', 'program-47', 

In [61]:
rca_uniq_values = train_df['rca'].unique()
print(set(rca_uniq_values))

{'rca-41', 'rca-80', 'rca-81', 'rca-22', 'rca-93', 'rca-111', 'rca-97', 'rca-76', 'rca-20', 'rca-77', 'rca-26', 'rca-102', 'rca-42', 'rca-30', 'rca-44', 'rca-115', 'rca-73', 'rca-36', 'rca-54', 'rca-83', 'rca-45', 'rca-98', 'rca-19', 'rca-67', 'rca-9', 'rca-49', 'rca-16', 'rca-33', 'rca-48', 'rca-61', 'rca-29', 'rca-70', 'rca-34', 'rca-43', 'rca-103', 'rca-94', 'rca-6', 'rca-57', 'rca-50', 'rca-72', 'rca-32', 'rca-69', 'rca-4', 'rca-39', 'rca-55', 'rca-60', 'rca-117', 'rca-56', 'rca-99', 'rca-86', 'rca-71', 'rca-90', 'rca-14', 'rca-92', 'rca-25', 'rca-112', 'rca-53', 'rca-11', 'rca-8', 'rca-18', 'rca-35', 'rca-113', 'rca-79', 'rca-95', 'rca-40', 'rca-46', 'rca-3', 'rca-24', 'rca-100', 'rca-65', 'rca-38', 'rca-63', 'rca-21', 'rca-23', 'rca-110', 'rca-17', 'rca-84', 'rca-82', 'rca-104', 'rca-31', 'rca-116', 'rca-52', 'rca-119', 'rca-58', 'rca-107', 'rca-12', 'rca-1', 'rca-118', 'rca-2', 'rca-89', 'rca-51', 'rca-5', 'rca-66', 'rca-75', 'rca-64', 'rca-105', 'rca-37', 'rca-109', 'rca-15', '

### Visualize the generated data set

Project Title Visualization

In [63]:
for col_name in budget_col_names:
    raw_val = train_df[[col_name]]
    chart_title = col_name + ' Histogram'
    xaxis_title = col_name + ' Counts'
    yaxis_title = 'Frequency'
    #chart_title = "District " + district_name + " Total Events by Month & SHIFT"
    
    # plot the histogram
    fig = px.histogram(raw_val, x=col_name, marginal="box", # can be `box`, `violin`
                   nbins=12)
    fig.update_layout(
        title = chart_title,
        autosize=False,
        width=1500,
        height=700,
        margin=dict(
            l=50,
            r=50,
            b=100,
            t=100,
            pad=4
            ),
        paper_bgcolor="white",
    )
    fig.show()

### Visualize Project Data

In [ ]:
for index in range(3):
    primary_col = budget_col_names[index]
    group_col = budget_col_names[index+1]
    
    chart_title = primary_col + ' Summary' + 'by ' + group_col
    
    xaxis_title = col_name + ' Counts'
    yaxis_title = 'Frequency'
    #chart_title = "District " + district_name + " Total Events by Month & SHIFT"
    
    # plot the histogram
    fig = px.histogram(raw_val, x=col_name, marginal="box", # can be `box`, `violin`
                   nbins=12)
    fig.update_layout(
        title = chart_title,
        autosize=False,
        width=1500,
        height=700,
        margin=dict(
            l=50,
            r=50,
            b=100,
            t=100,
            pad=4
            ),
        paper_bgcolor="white",
    )
    fig.show()

# PHASE 3: RANDOMIZE EXECUTION DATA 

Section to build out the test data and functions

# END OF PROGRAM

"Si vacem para bellum"

# TEST SECTION

In [1]:
num_exe_proj = 15
num_exe_subproj = 30
num_exe_rca = 50
num_exe_program = 75

num_of_kc = 10
is_base = 1
is_nip = 1

In [2]:
exe_proj_list = ['proj-' + str(x) for x in range(num_exe_proj)]
exe_proj_list[:5]

['proj-0', 'proj-1', 'proj-2', 'proj-3', 'proj-4']

In [3]:
exe_subproj_list = ['subproj-' + str(x) for x in range(num_exe_subproj)]
exe_subproj_list[:5]

['subproj-0', 'subproj-1', 'subproj-2', 'subproj-3', 'subproj-4']

In [4]:
exe_rca_list = ['rca-' + str(x) for x in range(num_exe_rca)]
exe_rca_list[:5]

['rca-0', 'rca-1', 'rca-2', 'rca-3', 'rca-4']

In [5]:
exe_prog_list = ['program-' + str(x) for x in range(num_exe_program)]
exe_prog_list[:5]

['program-0', 'program-1', 'program-2', 'program-3', 'program-4']

# PHASE 4: EXPORT DATA

In [5]:
train_df.to_csv(r'locked_random_data_v1', index = False)